In [1]:
import numpy as np
import pandas as pd

In [2]:
df_transactions = pd.read_csv('user_transactions_Uzhhorod.csv')

In [3]:
in_area = pd.read_csv('output.csv', usecols=[1])

In [4]:
df_full = pd.concat([df_transactions, in_area], axis=1)
df_full.columns = ['user_id', 'event_dt', 'lat', 'lon',	'in_area']
df_full['in_area'] = df_full['in_area'].astype(float)
df_full.sort_values(by=['user_id', 'event_dt'], inplace=True)
df_full.head()

user_id             event_dt        lat        lon  in_area
73004   100275  2020-09-01 00:04:42  50.450253  30.529755      0.0
73015   100275  2020-09-01 00:04:44  50.450253  30.529755      0.0
73214   100275  2020-09-01 00:34:42  50.450253  30.529755      0.0
73418   100275  2020-09-01 00:34:44  50.450253  30.529755      0.0
72773   100275  2020-09-01 01:04:42  50.450253  30.529755      0.0

In [5]:
start_points = []
end_points = []

def difference(window):
    global start_points
    global end_points

    if window.iloc[0] != window.iloc[1]:

        start_points += [window.index[0]]
        end_points += [window.index[1]]

    return 0


_ = df_full['in_area'].rolling(2, min_periods=2).apply(difference)

In [6]:
start_coords = df_full.loc[start_points, ['lat', 'lon']].values.tolist()
finish_coords = df_full.loc[end_points, ['lat', 'lon']].values.tolist()


In [7]:
import numpy as np

centroid_lat = 48.61936276498121
centroid_lon = 22.29484948394689

near_start_coords = []
near_finish_coords = []

for begin, end in zip(start_coords, finish_coords):
    # if np.sqrt((begin[0] - centroid_lat) ** 2 + (begin[1] - centroid_lon) ** 2) < 0.2 \
    #     and np.sqrt((end[0] - centroid_lat) ** 2 + (end[1] - centroid_lon) ** 2) < 0.2:

    if np.sqrt((begin[0] - end[0]) ** 2 + (begin[1] - end[1]) ** 2) < 0.02:
        
        near_start_coords += [begin]
        near_finish_coords += [end]


In [8]:
df_bounds = pd.read_csv('bounds.csv', usecols=[1, 2])

In [9]:
import folium
import pandas as pd

this_map = folium.Map(prefer_canvas=True)
    
folium.PolyLine(df_bounds[['lon', 'lat']].values.tolist(), weight=3, color='red').add_to(this_map)

for i in range(10000):
    folium.PolyLine(locations=[near_start_coords[i]]+[near_finish_coords[i]], weight=0.1).add_to(this_map)
    # folium.PolyLine(locations=[start_coords[i]]+[finish_coords[i]], weight=2).add_to(this_map)

this_map.fit_bounds(this_map.get_bounds())

this_map